## Machine Learning to Predict *Bombus* Species Names Given Their Coordinates
The program used `records` library to download occurrence data of three Bombus species: *occidentalis* *pensylvanicus* and *terricola*, which contained the longitude and latitude of the samples found. Here with these information, the program adopted the `KNeighborsClassifier` model from the `scikit-learn` library so that it could predict the species names if the longitude & latitude information is provided.

### 1. Download the data
Use the `records` library to download a series of occurrence records for *Bombus Occidentalis* (taxon key: 1340429), *Bombus pensylvanicus* (taxon key: 1340416), and *Bombus terricola* (taxon key: 1340493).

In [1]:
import records

In [2]:
# Download data for occidentalis
kwargs = {"taxonKey": "1340429"}
occidentalis_data = records.Records("Bombus", interval=(1980, 2000), **kwargs)

In [7]:
occidentalis_data.df.shape

(2315, 112)

In [51]:
# Download data for pensylvanicus
kwargs = {"taxonKey": "1340416"}
pensylvanicus_data = records.Records("Bombus", interval=(1980, 2000), **kwargs)

In [52]:
pensylvanicus_data.df.shape

(2099, 116)

In [77]:
# Download data for terricola
kwargs = {"taxonKey": "1340493"}
terricola_data = records.Records("Bombus", interval=(1970, 2000), **kwargs)

In [78]:
terricola_data.df.shape

(2038, 108)

### 2. Prepare the data
Here we fetched three keys for each sample: `species`, `decimal longitude` and `decimal latitude`. We concatenated the three data sets together and shuffled them to form the overall data set for training and setting. Then we specified `decimal longitude` and `decimal latitude` as features, and `species` as the label. Finally, we separated test data and training data.

In [10]:
import numpy as np
import pandas as pd
import toyplot
toyplot.config.autoformat = "html"

In [53]:
o_data = occidentalis_data.df[["species", "decimalLongitude", "decimalLatitude"]]
o_data.head()

species  decimalLongitude  decimalLatitude
0  Bombus occidentalis        -111.83000         41.73000
1  Bombus occidentalis        -103.82278         42.75806
2  Bombus occidentalis        -117.53470         47.79520
3  Bombus occidentalis        -103.82278         42.75806
4  Bombus occidentalis        -103.82278         42.75806

In [54]:
i_data = pensylvanicus_data.df[["species", "decimalLongitude", "decimalLatitude"]]
i_data.head()

species  decimalLongitude  decimalLatitude
0  Bombus pensylvanicus         -88.12140         37.97490
1  Bombus pensylvanicus         -87.78013         40.08299
2  Bombus pensylvanicus         -88.29000         42.17000
3  Bombus pensylvanicus         -90.93620         40.98490
4  Bombus pensylvanicus        -105.55100         38.99790

In [79]:
t_data = terricola_data.df[["species", "decimalLongitude", "decimalLatitude"]]
t_data.head()

species  decimalLongitude  decimalLatitude
0  Bombus terricola         -84.74758         45.55102
1  Bombus terricola         -84.79261         45.62301
2  Bombus terricola         -84.79261         45.62301
3  Bombus terricola         -84.79261         45.62301
4  Bombus terricola         -84.79261         45.62301

In [80]:
# Concatenate and shuffle the data
data = pd.concat([o_data, i_data, t_data])
data = data.sample(frac=1).reset_index(drop=True)
data.head(10)

species  decimalLongitude  decimalLatitude
0  Bombus pensylvanicus        -96.471800        42.203700
1  Bombus pensylvanicus        -89.870000        40.410000
2   Bombus occidentalis       -148.301500        64.704000
3      Bombus terricola        -76.538550        42.553680
4      Bombus terricola        -84.792610        45.623010
5   Bombus occidentalis       -110.589749        43.934762
6   Bombus occidentalis       -123.555497        42.365499
7   Bombus occidentalis       -122.528010        41.594740
8   Bombus occidentalis       -122.137222        47.037604
9   Bombus occidentalis       -111.618900        41.775000

In [83]:
# plot the total data to see how it looks like
cmap = {"Bombus pensylvanicus": "pink", "Bombus occidentalis": "grey", "Bombus terricola": "skyblue"}
toyplot.scatterplot(
    data.decimalLongitude, 
    data.decimalLatitude, 
    opacity=0.5,
    color=[cmap[i] for i in data.species], 
    width=300, 
    height=250);

<g class="toyplot-Datum" style="fill:rgb(52.9%,80.8%,92.2%);fill-opacity:1.0;opacity:0.5;stroke:rgb(52.9%,80.8%,92.2%);stroke-opacity:1.0" transform="translate(228.80527067800

In [84]:
# prepare the data features x and label y
x = data[["decimalLongitude", "decimalLatitude"]].values
y = data.species.values
data[["decimalLongitude", "decimalLatitude"]].shape

(6452, 2)

In [85]:
# for overall 6452 samples, we chose the first 452 data points as test, 
# and all the rest data points as training.
ntest = 452
xtest = x[:ntest]
xtrain = x[ntest:]
ytest = y[:ntest]
ytrain = y[ntest:]

### 3. Initialize a model instance
Select `kNeighborsClassifier` from `scikit-learn` library and create an instance.

In [86]:
from sklearn.neighbors import KNeighborsClassifier

In [87]:
knn = KNeighborsClassifier(n_neighbors=1)

### 4. Fit the model
Train the model on the training data set.

In [88]:
knn.fit(xtrain, ytrain)

KNeighborsClassifier(algorithm='auto', leaf_size=30, metric='minkowski',
           metric_params=None, n_jobs=1, n_neighbors=1, p=2,
           weights='uniform')

### 5. Get predictions
Apply the model to the test data set, predicting the label from features.

In [89]:
yfit = knn.predict(xtest)

### 6. Assess the goodness of fit 
Measure the accuracy of the model by comparing the predicted values to the actual labels in the test. And we used cross validation to optimize the model.

In [90]:
np.mean(yfit == ytest)

0.9867256637168141

In [91]:
cmap = {"Bombus pensylvanicus": "pink", "Bombus occidentalis": "grey", "Bombus terricola": "skyblue"}
c, a, m = toyplot.scatterplot(
    data.decimalLongitude,
    data.decimalLatitude,
    opacity=0.5,
    color=[cmap[i] for i in data.species],
    width=300,
    height=250
);
a.scatterplot(
    xtest[:, 0], xtest[:, 1], size=8, 
    mstyle={"stroke": 'black'},
    color=[cmap[i] for i in ytest],
);

<g class="toyplot-Datum" style="fill:rgb(52.9%,80.8%,92.2%);fill-opacity:1.0;opacity:0.5;stroke:rgb(52.9%,80.8%,92.2%);stroke-opacity:1.0" transform="translate(228.80527067800

In [92]:
# Cross validation to optimize the model 
cvs = np.zeros(200)
for k in range(1, 200):
    knn = KNeighborsClassifier(n_neighbors=k)
    knn.fit(xtrain, ytrain)
    yfit = knn.predict(xtest)
    cvs[k] = np.mean(yfit == ytest)

In [93]:
toyplot.plot(cvs, height=300, width=350, ymin=0.75);

<path d="M 50.0 850.0 L 51.25 60.619469026548686 L 52.5 60.619469026548686 L 53.75 62.389380530973426 L 55.0 60.619469026548686 L 56.25 60.619469026548686 L 57.5 58.84955752212386 L 58.75 62.389380530973426 L 60.0 64.15929203539825 L 61.25 65.92920353982299 L 62.5 67.69911504424782 L 63.75 65.92920353982299 L 65.0 67.69911504424782 L 66.25 67.69911504424782 L 67.5 67.69911504424782 L 68.75 67.69911504424782 L 70.0 65.92920353982299 L 71.25 65.92920353982299 L 72.5 69.46902654867256 L 73.75 69.46902654867256 L 75.0 69.46902654867256 L 76.25 69.46902654867256 L 77.5 71.23893805309737 L 78.75 67.69911504424782 L 80.0 67.69911504424782 L 81.25 69.46902654867256 L 82.5 69.46902654867256 L 83.75 65.92920353982299 L 85.0 65.92920353982299 L 86.25 67.69911504424782 L 87.5 69.46902654867256 L 88.75 69.46902654867256 L 90.0 71.23893805309737 L 91.25 71.23893805309737 L 92.5 71.23893805309737 L 93.75 71.23893805309737 L 95.0 73.00884955752211 L 96.25 73.00884955752211 L 97.5 76.54867256637168 L 98.75 76.54867256637168 L 100.0 76.54867256637168 L 101.25 76.54867256637168 L 102.5 76.54867256637168 L 103.75 85.39823008849554 L 105.0 83.6283185840708 L 106.25 87.16814159292036 L 107.5 81.85840707964599 L 108.75 81.85840707964599 L 110.0 74.77876106194694 L 111.25 74.77876106194694 L 112.5 74.77876106194694 L 113.75 74.77876106194694 L 115.0 76.54867256637168 L 116.25 74.77876106194694 L 117.5 74.77876106194694 L 118.75 74.77876106194694 L 120.00000000000001 74.77876106194694 L 121.25 76.54867256637168 L 122.5 78.3185840707965 L 123.75 78.3185840707965 L 125.0 76.54867256637168 L 126.25 76.54867256637168 L 127.5 76.54867256637168 L 128.75 76.54867256637168 L 130.0 76.54867256637168 L 131.25 76.54867256637168 L 132.5 76.54867256637168 L 133.75 78.3185840707965 L 135.0 78.3185840707965 L 136.25 78.3185840707965 L 137.5 78.3185840707965 L 138.75 78.3185840707965 L 140.0 78.3185840707965 L 141.25 78.3185840707965 L 142.5 78.3185840707965 L 143.75 78.3185840707965 L 145.0 78.3185840707965 L 146.25 78.3185840707965 L 147.5 78.3185840707965 L 148.75 78.3185840707965 L 150.0 78.3185840707965 L 151.25 78.3185840707965 L 152.5 78.3185840707965 L 153.75 78.3185840707965 L 155.0 78.3185840707965 L 156.25 78.3185840707965 L 157.5 78.3185840707965 L 158.75 78.3185840707965 L 160.0 78.3185840707965 L 161.25 78.3185840707965 L 162.5 78.3185840707965 L 163.75 78.3185840707965 L 165.0 78.3185840707965 L 166.25 78.3185840707965 L 167.5 78.3185840707965 L 168.75 78.3185840707965 L 170.0 78.3185840707965 L 171.25 78.3185840707965 L 172.5 78.3185840707965 L 173.75 78.3185840707965 L 175.0 78.3185840707965 L 176.25 78.3185840707965 L 177.5 78.3185840707965 L 178.75 78.3185840707965 L 180.0 78.3185840707965 L 181.25 78.3185840707965 L 182.5 78.3185840707965 L 183.75 78.3185840707965 L 185.0 78.3185840707965 L 186.25 78.3185840707965 L 187.5 78.3185840707965 L 188.75000000000003 78.3185840707965 L 190.00000000000003 78.3185840707965 L 191.24999999999997 78.3185840707965 L 192.49999999999997 78.3185840707965 L 193.75 78.3185840707965 L 195.0 78.3185840707965 L 196.25 78.3185840707965 L 197.5 78.3185840707965 L 198.75 78.3185840707965 L 200.0 78.3185840707965 L 201.25 78.3185840707965 L 202.5 78.3185840707965 L 203.75 78.3185840707965 L 205.0 78.3185840707965 L 206.25 78.3185840707965 L 207.5 78.3185840707965 L 208.75 78.3185840707965 L 210.0 78.3185840707965 L 211.25 78.3185840707965 L 212.5 78.3185840707965 L 213.75 78.3185840707965 L 215.0 78.3185840707965 L 216.25 78.3185840707965 L 217.5 78.3185840707965 L 218.75 78.3185840707965 L 220.00000000000003 78.3185840707965 L 221.25000000000003 76.54867256637168 L 222.49999999999997 76.54867256637168 L 223.74999999999997 76.54867256637168 L 225.0 76.54867256637168 L 226.25 76.54867256637168 L 227.5 76.54867256637168 L 228.75 76.54867256637168 L 230.0 76.54867256637168 L 231.25 76.54867256637168 L 232.5 76.54867256637168 L 233.75 76.54867256637168 L 235.0 76.54867256637168 L 236.25 76.54867256637168 L 237.5 74.77876106194

In [94]:
cvs.argmax()

6

In [95]:
knn = KNeighborsClassifier(n_neighbors=cvs.argmax())
knn.fit(xtrain, ytrain)
yfit = knn.predict(xtest)
np.mean(yfit == ytest) # Give the score of the test.

0.9889380530973452

In [96]:
cmap = {"Bombus pensylvanicus": "pink", "Bombus occidentalis": "grey", "Bombus terricola": "skyblue"}
c, a, m = toyplot.scatterplot(
    data.decimalLongitude,
    data.decimalLatitude,
    opacity=0.5,
    color=[cmap[i] for i in data.species],
    width=300,
    height=250
);
a.scatterplot(
    xtest[:, 0], xtest[:, 1], size=8, 
    mstyle={"stroke": 'black'},
    color=[cmap[i] for i in ytest])

<g class="toyplot-Datum" style="fill:rgb(52.9%,80.8%,92.2%);fill-opacity:1.0;opacity:0.5;stroke:rgb(52.9%,80.8%,92.2%);stroke-opacity:1.0" transform="translate(228.80527067800

### 7. Summary
I focused on the occurrence data of three Bombus species: *occidentalis* *pensylvanicus* and *terricola*. I used their species names as labels, and their longitude and latitude as features. I developed the knn model to predict the species identity based on their coordinate information. After cross validation (let `n_neighbors` be 6), we got the test score 0.9889380530973452, which indicated this is a good model for prediction.